In [ ]:
import gradio as gr
import numpy as np
from os import environ
from PIL import Image as PImage
from torchvision import transforms as T
from transformers import MaskFormerForInstanceSegmentation, MaskFormerImageProcessor

In [ ]:
ade_mean=[0.485, 0.456, 0.406]
ade_std=[0.229, 0.224, 0.225]

palette = [
    [120, 120, 120], [4, 200, 4], [4, 4, 250], [6, 230, 230],
    [80, 50, 50], [120, 120, 80], [140, 140, 140], [204, 5, 255]
]

model_id = f"thiagohersan/maskformer-satellite-trees"

vegetation_labels = ["vegetation"]

In [ ]:
def visualize_instance_seg_mask(img_in, mask, id2label, included_labels):
    img_out = np.zeros((mask.shape[0], mask.shape[1], 3))
    image_total_pixels = mask.shape[0] * mask.shape[1]
    label_ids = np.unique(mask)

    id2color = {id: palette[id] for id in label_ids}
    id2count = {id: 0 for id in label_ids}

    for i in range(img_out.shape[0]):
      for j in range(img_out.shape[1]):
        img_out[i, j, :] = id2color[mask[i, j]]
        id2count[mask[i, j]] = id2count[mask[i, j]] + 1

    image_res = (0.5 * img_in + 0.5 * img_out).astype(np.uint8)

    dataframe = [[
        f"{id2label[id]}",
        f"{(100 * id2count[id] / image_total_pixels):.2f} %",
        f"{np.sqrt(id2count[id] / image_total_pixels):.2f} m"
        ] for id in label_ids if id2label[id] in included_labels]

    if len(dataframe) < 1:
        dataframe = [[
            f"",
            f"{(0):.2f} %",
            f"{(0):.2f} m"
        ]]

    return image_res, dataframe


In [ ]:
# preprocessor = MaskFormerImageProcessor.from_pretrained(model_id)
preprocessor = MaskFormerImageProcessor(
    do_resize=False,
    do_normalize=False,
    do_rescale=False,
    ignore_index=255,
    do_reduce_labels=False
)

hf_token = environ.get('HFTOKEN') or True
model = MaskFormerForInstanceSegmentation.from_pretrained(model_id, use_auth_token=hf_token)

test_transform = T.Compose([
    T.ToTensor(),
    T.Normalize(mean=ade_mean, std=ade_std)
])

with PImage.open("../color-filter-calculator/assets/Artshack_screen.jpg") as img:
    img_size = (img.height, img.width)
    norm_image = test_transform(np.array(img))
    inputs = preprocessor(images=norm_image, return_tensors="pt")
    

In [ ]:
outputs = model(**inputs)

In [ ]:
results = preprocessor.post_process_semantic_segmentation(outputs=outputs, target_sizes=[img_size])[0]
mask_img, dataframe = visualize_instance_seg_mask(np.array(img), results.numpy(), model.config.id2label, vegetation_labels)

In [ ]:
dataframe